In [9]:
base_dataset_path = '../../datasets/ren_et_al/'

dataset_name_path = 'figer/'

types_list_path = 'all_types.txt'

train_path = 'train.json'
dev_path = 'dev.json'
test_path = 'test.json'

dir_for_partitioned_datasets = '../../datasets/datasets_for_incremental_training/'

In [11]:
# import types
with open(base_dataset_path + dataset_name_path + types_list_path, 'r') as inp:
    types_list = [l.replace('\n', '') for l in inp.readlines()]
types_list

['/art',
 '/art/film',
 '/astral_body',
 '/award',
 '/biology',
 '/body_part',
 '/broadcast',
 '/broadcast/tv_channel',
 '/broadcast_network',
 '/broadcast_program',
 '/building',
 '/building/airport',
 '/building/dam',
 '/building/hospital',
 '/building/hotel',
 '/building/library',
 '/building/power_station',
 '/building/restaurant',
 '/building/sports_facility',
 '/building/theater',
 '/chemistry',
 '/computer',
 '/computer/algorithm',
 '/computer/programming_language',
 '/disease',
 '/education',
 '/education/department',
 '/education/educational_degree',
 '/event',
 '/event/attack',
 '/event/election',
 '/event/military_conflict',
 '/event/natural_disaster',
 '/event/protest',
 '/event/sports_event',
 '/event/terrorist_attack',
 '/finance',
 '/finance/currency',
 '/finance/stock_exchange',
 '/food',
 '/game',
 '/geography',
 '/geography/glacier',
 '/geography/island',
 '/geography/mountain',
 '/god',
 '/government',
 '/government/government',
 '/government/political_party',
 '/gov

In [14]:
# read dataset
import json
with open(base_dataset_path + dataset_name_path + train_path, 'r') as inp:
    lines = [json.loads(l) for l in inp.readlines()]

In [15]:
len(lines)

2676846

In [16]:
# declare types to filter
types_to_filter = ['/location']

In [17]:
from collections import defaultdict
from tqdm import tqdm

# create dataset with the examples annotated with only the types_to_filter 
# or annotated with other types that are not sons of types_to_filter

new_dataset_partitions = defaultdict(list)
new_dataset_partitions['only_father'] = defaultdict(list)
new_dataset_partitions['father_and_sons'] = defaultdict(list)

types_only_partitions = defaultdict(list)
types_only_partitions['only_father'] = defaultdict(list)                
types_only_partitions['father_and_sons'] = defaultdict(list)                

for l in tqdm(lines):
    line_types = l['y_str']
    if all([t not in line_types for t in types_to_filter]):
        new_dataset_partitions['disjoint'].append(l)
        types_only_partitions['disjoint'].append(line_types)
    else:
        for t in types_to_filter:
            if sum([t in line_type for line_type in line_types ]) == 1:
                new_dataset_partitions['only_father'][t].append(l)
                types_only_partitions['only_father'][t].append(line_types)
            else:
                for lt in line_types:
                    if t in lt and lt != t:
                        new_dataset_partitions['father_and_sons'][lt].append(l)
                        types_only_partitions['father_and_sons'][lt].append(line_types)
                

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2676846/2676846 [00:03<00:00, 728940.44it/s]


In [18]:
types_only_partitions['disjoint']

[['/person', '/person/actor', '/person/artist'],
 ['/event'],
 ['/broadcast_program'],
 ['/person'],
 ['/person'],
 ['/person', '/person/artist', '/person/author', '/person/musician'],
 ['/person', '/person/artist'],
 ['/person', '/person/actor', '/person/artist', '/person/musician'],
 ['/music', '/person', '/person/artist', '/person/author', '/person/musician'],
 ['/music', '/person', '/person/artist', '/person/author', '/person/musician'],
 ['/music'],
 ['/person',
  '/person/actor',
  '/person/artist',
  '/person/author',
  '/person/director'],
 ['/person', '/person/artist', '/person/musician'],
 ['/product', '/product/weapon'],
 ['/person', '/person/actor', '/person/artist'],
 ['/organization', '/organization/company'],
 ['/music'],
 ['/music'],
 ['/music'],
 ['/music'],
 ['/person',
  '/person/actor',
  '/person/artist',
  '/person/author',
  '/person/musician'],
 ['/music'],
 ['/music'],
 ['/art', '/art/film', '/music', '/play', '/written_work'],
 ['/person', '/person/artist', '/

In [19]:
types_only_partitions['father_and_sons'].keys()

dict_keys(['/location/city', '/location/country', '/location/cemetery', '/location/province', '/location/county', '/location/body_of_water', '/location/bridge'])

In [20]:
types_only_partitions['father_and_sons']['/location/country']

[['/location', '/location/country'],
 ['/government_agency',
  '/language',
  '/location',
  '/location/cemetery',
  '/location/country',
  '/person',
  '/person/artist',
  '/title'],
 ['/government_agency',
  '/location',
  '/location/country',
  '/person',
  '/person/author'],
 ['/government',
  '/government/government',
  '/language',
  '/location',
  '/location/country',
  '/person',
  '/person/author'],
 ['/geography',
  '/geography/island',
  '/government',
  '/government/government',
  '/location',
  '/location/country'],
 ['/government', '/government/government', '/location', '/location/country'],
 ['/government', '/government/government', '/location', '/location/country'],
 ['/location', '/location/country'],
 ['/government_agency',
  '/language',
  '/location',
  '/location/cemetery',
  '/location/country',
  '/person',
  '/person/artist',
  '/title'],
 ['/government', '/government/government', '/location', '/location/country'],
 ['/government',
  '/government/government',
  

In [21]:
types_only_partitions['only_father']

defaultdict(list,
            {'/location': [['/location',
               '/metropolitan_transit',
               '/metropolitan_transit/transit_line'],
              ['/location'],
              ['/location', '/transportation', '/transportation/road'],
              ['/building',
               '/location',
               '/organization',
               '/organization/company'],
              ['/building', '/building/airport', '/location'],
              ['/building', '/location', '/park'],
              ['/location', '/news_agency', '/written_work'],
              ['/location'],
              ['/building', '/location'],
              ['/location',
               '/organization',
               '/organization/educational_institution'],
              ['/location',
               '/organization',
               '/organization/educational_institution'],
              ['/geography', '/geography/island', '/location'],
              ['/language', '/location'],
              ['/location',
  

In [22]:
len(lines)

2676846

In [23]:
len(types_only_partitions['disjoint'])

1554393

In [24]:
len(new_dataset_partitions['disjoint'])

1554393

In [25]:
len(new_dataset_partitions['only_father']['/location'])

356937

In [26]:
types_only_partitions['father_and_sons'].keys()

dict_keys(['/location/city', '/location/country', '/location/cemetery', '/location/province', '/location/county', '/location/body_of_water', '/location/bridge'])

In [28]:
new_dataset_partitions['father_and_sons']

defaultdict(list,
            {'/location/city': [{'left_context_token': ['"',
                "'",
                'Angels',
                'Flight',
                '"',
                ',',
                'Third',
                '&amp;',
                'amp',
                ';',
                'Hill',
                'Streets',
                ','],
               'mention_span': 'Los Angeles',
               'right_context_token': [',',
                'Los',
                'Angeles',
                'County',
                ',',
                'CA',
                'Historic',
                'American',
                'Buildings',
                'SurveyHABS',
                'CAL,19-LOSAN',
                ',13',
                '-',
                'http://memory.loc.gov/pnp/habshaer/ca/ca0200/ca0209/photos/011992pv.jpg'],
               'y_str': ['/location', '/location/city']},
              {'left_context_token': ['"',
                '1',
                ',',
    

In [29]:
for k in types_only_partitions['father_and_sons'].keys():
    print(len(types_only_partitions['disjoint']) + len(types_only_partitions['only_father']['/location']) + len(types_only_partitions['father_and_sons'][k]))

2281492
2165406
2002722
1997513
1962637
1946370
1912979


In [49]:
pretraining_datasets = {}
for father in types_to_filter:
    with open(dir_for_partitioned_datasets + dataset_name_path + 'pretraining_' + father.replace('/', '') + '_dev.json', 'w') as out:
        for disjoint_line in tqdm(new_dataset_partitions['disjoint']):
            json.dump(disjoint_line, out)
            out.write('\n')
        for of_line in tqdm(new_dataset_partitions['only_father'][father]):
            json.dump(of_line, out)
            out.write('\n')
#     pretraining_dataset = {}
    for son in new_dataset_partitions['father_and_sons'].keys():
        with open(dir_for_partitioned_datasets + dataset_name_path + 'incremental_' + son.replace('/', '') + '_dev.json', 'w') as out:
            for son_examples in tqdm(new_dataset_partitions['father_and_sons'][son]):
                son_examples['y_str'] = [father, son]
                json.dump(son_examples, out)
                out.write('\n')                

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 6069.90it/s]
